In [2]:
from load_netmob_data import load_subway_shp,load_netmob_gdf,find_ids_within_epsilon
import torch

# Load subway gdf adn NetMob gdf
ref_subway = load_subway_shp()
Netmob_gdf = load_netmob_gdf()

# Get Cell-Id within epsilon : 
result,joined = find_ids_within_epsilon(Netmob_gdf,ref_subway,epsilon=1000)  #epsilon : 1km
maxi_nb_tile =  result.apply(lambda row: len(row.tile_id),axis=1).max()
print(f"Maximum number of NetMob Cell associated to a subway station: {maxi_nb_tile}")
joined.explore('COD_TRG')

Maximum number of NetMob Cell associated to a subway station: 318


In [42]:
from os import listdir
import os 
import glob 
import pandas as pd 
import torch.nn.functional as F
from datetime import datetime,timedelta

folder_path = '../../Data/NetMob/'
apps = [app for app in listdir(folder_path) if ((app != 'Lyon.geojson') and (not app.startswith('.'))) ]   # Avoid hidden folder and Lyon.geojson
metadata = {result['COD_TRG'][station_ind] : {} for station_ind in range(len(result))}

# For each app
for app in apps: 
    folder_days = [day for day in listdir(f'{folder_path}/{app}') if (not day.startswith('.')) ]

    # for each days  
    for day in folder_days:
        txt_paths = sorted(glob.glob(os.path.join(f'{folder_path}/{app}/{day}', "*.txt")))

        # For each transfert mode:
        for path in txt_paths:
            transfer_mode = path.split('.')[-2].split('_')[-1]

            day_str = str(day)
            day_str = datetime.strptime(day_str, '%Y%m%d')
            times = [day_str + timedelta(minutes=15*i) for i in range(96)]
            times_str = [t.strftime('%H:%M') for t in times]
            columns = ['tile_id'] + times_str

            # Loop through each station. Get associated usefull Tile-id
            for station_ind in range(len(result)):
                T =  torch.Tensor(pd.read_csv(path, sep = ' ', names = columns).set_index(['tile_id']).loc[result.tile_id[station_ind]].values).to(dtype = torch.int32) 
                padding = maxi_nb_tile-T.size(0)

                if padding > 0:
                    T = F.pad(T,(0,0,0,padding),'constant',0)
                Tensors.append(T)
            Tensors = torch.stack(Tensors,dim = 0)
            break
        break
    break



        #print(f'app {app}fini')
    #print(f"Station {result['COD_TRG'][station_ind]} fini")

NameError: name 'maxi_nb_tile' is not defined

In [37]:
torch.Tensor(pd.read_csv(path, sep = ' ', names = columns).set_index(['tile_id']).loc[result.tile_id[station_ind]].values).size()

torch.Size([316, 96])

In [41]:
T = torch.Tensor(pd.read_csv(path, sep = ' ', names = columns).set_index(['tile_id']).loc[result.tile_id[station_ind]].values)
T.max(),T.min(),T.median()

(tensor(509789, dtype=torch.int32),
 tensor(0, dtype=torch.int32),
 tensor(1341, dtype=torch.int32))

In [16]:
metadata[result['COD_TRG'][station_ind]]['tile_id'] = df.index
metadata[result['COD_TRG'][station_ind]]['days'] =
metadata[result['COD_TRG'][station_ind]]['apps'] = 
metadata[result['COD_TRG'][station_ind]]['mode_transfer'] = 